# OOS Predictions

Example Notebook of how are we gettins results from model Training. In our final solution we have many more files and scripts we need to showcase. 

## Libraries

In [0]:
from pyspark.sql.functions import *
from pyspark.sql import Window

## DF

In [0]:
df = spark.read.table("gold_sandbox.poc_oos_gold.prophet_forecast")
complete_df = spark.read.table("gold_sandbox.poc_oos_gold.train_sample_5_stores")

## Split Train Valid

In [0]:
split_date = "2017-07-16"

train_sdf = (complete_df
.filter(col("date") < split_date)
.select("store_nbr","item_nbr","date","total_sales"))

valid_sdf = (complete_df
.filter(col("date") >= split_date)
.select("store_nbr","item_nbr","date","total_sales"))

## Get Prophet Predictions

In [0]:
df_clean = (df
.withColumnRenamed("ds","date")    
.drop("model_name","run_ts"))

predictions = (df_clean
.join(valid_sdf, on=['item_nbr','store_nbr','date'], how = 'left')
.withColumn("yhat", when(col("yhat") < 0, 0).otherwise(col("yhat"))))

## Calculate MAPE

In [0]:
mape = (predictions
.withColumn("ape",abs(try_divide((col("total_sales") + 1) - (col("yhat") + 1),col("total_sales") + 1)))
.groupBy("store_nbr", "item_nbr")
.agg(mean("ape").alias("MAPE")))

display(mape)

store_nbr item_nbr MAPE 44 227111 0.2046826906973099 47 96995 0.879971238462436 47 268676 0.3405648065375247 47 115850 1.4891573587018543 47 214859 1.1058907163217568 3 1950170 0.35901310492440813 3 1972673 0.4052323161204203 49 1354389 0.4573791532287049 3 1354382 0.4648978427227964 3 1421428 7.5894601494202005 3 1575245 0.554339276368522 45 841614 1.473475523584174 47 1259006 0.6286618922410343 49 1388559 0.4531466572925111 3 1970207 1.2121388996537492 44 2013309 0.8377368117976971 49 1609724 0.45922382260448846 47 1939424 0.3486331036988392 47 1400329 0.6179500855424391 49 1312957 0.5974393477954145 47 859932 0.5469771858432185 49 1463881 0.5387149311538139 44 658609 0.7873157280623236 45 729337 0.2529831926922792 45 949511 0.34379976688192165 45 1464082 0.7798670050284829 3 269287 1.2958580126075152 49 518091 19.041010612813814 44 716250 5.11844794578534 47 750856 0.8112108452085717 44 1371395 0.09074074074074073 3 2054635 0.8057077592277024 45 888682 0.8192488723708821 49 986193 0.5938023947938759 45 1092061 0.383251418213119 44 1937083 0.5973755194734232 3 1047775 1.1434501735259452 3 1346636 0.6781745378504074 49 1373394 0.4182696522996864 44 322094 0.7644913171769648 44 1457202 0.781539155634659 3 1909412 0.12141827838220336 45 1230327 0.042120735785778796 47 1243817 0.13737593451136004 47 1410792 0.12303936645649928 49 1229440 0.45960794121292625 3 2017343 0.7784161097587509 3 2037008 1.0284196778320291 47 215332 0.8404068753384516 49 2081050 0.32210772993805853 3 1109116 0.14512577205557134 45 527757 0.8546385342080337 44 1464137 1.2965317817197928 47 671055 1.1990290811606357 45 1047679 0.4353732892681867 49 207857 1.0228485951516744 44 886396 1.0536112218311438 47 1920059 0.5570258436966548 49 1060036 0.7202474689576273 45 1458849 0.5684845521316523 45 1999969 1.1708192621557099 45 1464087 0.9468129252900478 49 692537 0.3022709058518306 45 1987653 0.6011130065372854 47 1418842 0.043510847060131946 47 269287 1.1964455884737921 45 2059799 0.6103346366945962 44 1999775 1.8036294488961837 45 2053874 0.3767357866391941 47 1660272 3.8172906864489438 3 724403 0.28128086374529476 3 1466288 0.4541700637238871 49 1157562 0.4078006534505135 45 2013648 0.8113080887412598 45 402136 0.9540247223975664 3 1386695 0.5871242073868643 45 939207 1.1522079051820042 45 2062912 2.2094197456444773 44 1943792 0.847852061824833 47 2010755 7.309891264228812 47 2026597 0.493214570139405 3 1392260 0.5882022414193242 44 374464 0.6033880483135903 45 402299 0.6661139013829884 47 1133955 0.19241878386967007 3 1047695 0.7913153054174785 47 1944334 0.936119477147939 47 1463790 0.653563040049212 47 1621529 1.092012703117696 45 463458 1.548257608670587 49 358561 0.6109137006790929 44 470762 0.5410381998034471 49 1916209 0.45870207032473215 45 1910611 2.7604209866339198 45 2054580 1.0220991537183193 47 1351227 0.7914041593645055 47 2004673 0.4872493822957275 45 823245 0.2527898425420913 49 1916165 1.4839491527245707 44 1430083 0.5731153716591978 44 1369875 0.4603465846005459 3 619965 0.5742571276331809 3 1369793 0.49226134356704987 47 1230418 0.7164079033449567 47 1463437 2.8610979831841634 45 1084881 0.3788321696248288 3 584076 0.6417395568420411 44 1422500 1.115415419697788 45 1114754 0.2780799817956128 49 1076066 0.3320604045207915 3 1958186 0.4381658735389065 45 1418844 0.616798660995817 3 1299616 0.9725090090878278 49 162066 0.49049202622138227 49 813167 1.0897608323417087 3 357963 0.35651309914024054 49 1118775 1.9353198194567252 49 1239846 0.9874610539808828 3 1047773 1.314997959487294 49 770461 0.6908352399966635 47 940590 0.5025454661836259 49 1345071 0.44457005857726994 47 559873 0.3505822495220948 49 671076 0.6196972630169637 47 518091 12.033171867626903 3 1114903 0.6356913225955186 45 1946311 0.5255705725603806 44 870545 3.3089527157508067 44 1005465 0.4100368468031442 44 1695925 1.3028003713046223 49 105693 1.0821922540482518 3 1464070 0.40784228782923176 47 2032088 0.2815930640854003 49 1112450 2.6197670782558307 47 1261376 0.455889023698

## Phantom Stock Flag and Poisson Confidence

In [0]:
df_phantom = (predictions
.withColumn("phantom_oos_flag",when((col("total_sales") == 0) &(col("yhat") >= 1),lit(1)).otherwise(lit(0)))
)

In [0]:

df_poisson = (df_phantom
.withColumn("poisson_p0",when(col("phantom_oos_flag") == 1,exp(-col("yhat")))
.otherwise(lit(None)))
.withColumn("poisson_confidence",when(col("phantom_oos_flag") == 1,1 - exp(-col("yhat")))
.otherwise(lit(0.0)))
)

Poisson confidence measures how likely it is that getting zero sales on a given day is normal given the expected demand. It is based on the idea that daily sales tend to follow a typical pattern: when the expected demand is high, selling nothing is very unlikely; when expected demand is low, zero sales are more common. A high Poisson confidence means that zero sales are very unlikely under normal conditions, which suggests a possible stockout or availability issue. A low Poisson confidence means that zero sales are expected and not necessarily a problem.

## Flag Proxy

In [0]:
w_fwd = (Window.partitionBy("store_nbr", "item_nbr").orderBy("date").rowsBetween(1, 3))

df_proxy = (df_poisson
.withColumn("future_sales_3d", sum(col("total_sales")).over(w_fwd))
.withColumn("proxy_oos", when((col("total_sales") == 0) & (col("future_sales_3d") > 0),1).otherwise(0))
)

In [0]:
display(df_proxy
.filter(col("phantom_oos_flag") == 1)
.groupBy("proxy_oos") 
.count() 
.show()
)

+---------+-----+
|proxy_oos|count|
+---------+-----+
|        1| 9498|
|        0|10147|
+---------+-----+



## Results of Alerts

In [0]:
w = Window.orderBy(col("poisson_confidence").desc())

df_ranked = (df_proxy
.filter(col("phantom_oos_flag") == 1)
.withColumn("conf_bucket", ntile(5).over(w))
)

(
df_ranked
.groupBy("conf_bucket") 
.agg(
avg("proxy_oos").alias("proxy_rate"),
count("*").alias("n")
) 
.orderBy("conf_bucket")
.show()
)

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


+-----------+------------------+----+
|conf_bucket|        proxy_rate|   n|
+-----------+------------------+----+
|          1| 0.319419699669127|3929|
|          2|0.4321710358869941|3929|
|          3|0.5390684652583354|3929|
|          4|0.5739373886485111|3929|
|          5|0.5528124204632222|3929|
+-----------+------------------+----+



This logic ranks all potential phantom stockout cases from highest to lowest Poisson confidence, meaning from most to least unlikely to have zero sales under normal demand. It then splits them into five equal-sized confidence groups (from highest to lowest) and calculates, for each group, how often a proxy stockout signal is observed. This allows us to verify whether higher Poisson confidence is consistently associated with a higher likelihood of true stockout behavior.

In [0]:
final_df = (df_proxy
.join(mape, on=['store_nbr','item_nbr'], how = 'left')
.drop("yhat_lower","yhat_upper","future_sales_3d")
.withColumn("model", lit("prophet"))
)

In [0]:
display(final_df)

store_nbr item_nbr date yhat total_sales phantom_oos_flag poisson_p0 poisson_confidence proxy_oos MAPE model 3 96995 2017-07-16 0.3667922102501817 2.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-07-17 0.3266689141667939 1.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-07-18 0.345665833848637 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-07-19 0.2900532934676467 1.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-07-20 0.3367305381973093 0.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-07-21 0.3310009174607189 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-07-22 0.3748305529991813 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-07-23 0.42283952618031495 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-07-24 0.3737716769350868 1.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-07-25 0.3827470235001489 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-07-26 0.3162478635747907 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-07-27 0.3514120769122051 3.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-07-28 0.3338024660776383 1.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-07-29 0.36565890138783613 1.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-07-30 0.401882478153132 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-07-31 0.34149796938195465 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-08-01 0.33989878559790426 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-08-02 0.2638257108316999 1.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-08-03 0.2906531432371822 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-08-04 0.2661518794521045 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-08-05 0.2927353991067201 1.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-08-06 0.32543903039489097 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-08-07 0.2633784298362667 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-08-08 0.26199171050867337 1.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-08-09 0.18801657926323134 1.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-08-10 0.21877626870973846 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-08-11 0.19994332435113366 2.0 0 null 0.0 0 0.3604505609380428 prophet 3 96995 2017-08-12 0.23378818749813945 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-08-13 0.27516190219272946 0.0 0 null 0.0 1 0.3604505609380428 prophet 3 96995 2017-08-14 0.22295929087874733 1.0 0 null 0.0 0 0.3604505609380428 prophet 3 103520 2017-07-16 3.281155392195035 6.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-17 2.9310170816304146 2.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-18 2.9520751880614426 9.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-19 3.7586865631912825 3.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-20 4.121133473983993 2.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-21 4.475046954549222 5.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-22 4.812297137881881 11.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-23 3.367821092023511 0.0 1 0.03446465089272126 0.9655353491072788 1 0.5685512973603776 prophet 3 103520 2017-07-24 3.0489025544414536 0.0 1 0.04741092676203775 0.9525890732379623 1 0.5685512973603776 prophet 3 103520 2017-07-25 3.0955773200815107 3.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-26 3.9225565622877565 9.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-27 4.300617974304963 5.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-28 4.666004871379679 6.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-29 5.011289337323413 5.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-30 3.572170884135127 1.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-07-31 3.2567260086708782 6.0 0 null 0.0 0 0.5685512973603776 prophet 3 103520 2017-08-01 3.305783406294227 2.0

## Get best Store-Item Results for show case

In [0]:
window_spec = Window.orderBy("mape")

cherry_picked_models = (final_df
.groupBy("store_nbr","item_nbr")
.agg(
    avg(col("MAPE")).alias("mape"),
    sum(col("phantom_oos_flag")).alias("phantom_oos"),
    sum(col("total_sales")).alias("total_sales")
    )
.filter(col("phantom_oos") > 0)
.filter(col("total_sales") > 100)
.withColumn("mape_rank", row_number().over(window_spec))
.filter("mape_rank <= 50")
.select("store_nbr","item_nbr")
.withColumn("cherry_picked_flag", lit(1))
)

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


In [0]:
display(cherry_picked_models)

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


store_nbr item_nbr cherry_picked_flag 47 1920107 1 44 1456912 1 49 1913600 1 45 1457001 1 47 1089163 1 45 1058820 1 49 1047717 1 47 658609 1 49 1157562 1 3 1239740 1 49 1463610 1 49 470625 1 47 1105214 1 3 108786 1 3 1239956 1 44 2029457 1 45 1977997 1 44 372369 1 3 215303 1 44 405304 1 49 502182 1 3 1081359 1 47 1284221 1 49 314881 1 49 1457183 1 49 651326 1 49 812725 1 47 1354388 1 44 1967642 1 3 752987 1 49 1346626 1 49 1012787 1 47 1333225 1 45 1324670 1 47 2010913 1 49 372369 1 47 1076155 1 45 742735 1 49 1457000 1 3 1466288 1 44 414455 1 45 577740 1 47 1428779 1 49 1609724 1 47 265700 1 49 617092 1 45 619965 1 45 890372 1 3 819195 1 47 2006779 1

In [0]:
cherry_picked_models_hist = (final_df
.join(cherry_picked_models,on=['store_nbr','item_nbr'],how='left')
.filter("cherry_picked_flag == 1"))

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


In [0]:
display(cherry_picked_models_hist)

/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/expressions.py:1134: UserWarning: WARN WindowExpression: No Partition Defined for Window operation! Moving all data to a single partition, this can cause serious performance degradation.
  warnings.warn(


store_nbr item_nbr date yhat total_sales phantom_oos_flag poisson_p0 poisson_confidence proxy_oos MAPE model cherry_picked_flag 3 108786 2017-07-16 6.466841410010473 4.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-17 4.249004785117846 4.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-18 3.601925034340034 1.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-19 4.617463280604917 5.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-20 2.9622645031198696 3.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-21 4.231767133865768 6.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-22 5.384444943590437 8.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-23 5.802930477556032 4.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-24 3.6685159352249137 0.0 1 0.025514306747509617 0.9744856932524903 1 0.4178135292556882 prophet 1 3 108786 2017-07-25 3.1144440391995847 3.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-26 4.230594484882704 3.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-27 2.6814631142222636 1.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-28 4.060224824435771 2.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-29 5.3230318072581655 4.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-30 5.850194862845316 8.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-07-31 3.82074211915829 3.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-01 3.365766136040814 6.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-02 4.573163459843679 5.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-03 3.105662331227304 3.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-04 4.554928240794709 3.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-05 5.875897774729324 11.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-06 6.447987536289494 4.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-07 4.449671738678981 5.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-08 4.011838956702432 3.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-09 5.222531869320288 5.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-10 3.74496572677975 5.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-11 5.171615531694975 4.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-12 6.458522926911829 5.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-13 6.9864703665471835 6.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 108786 2017-08-14 4.935517173792379 3.0 0 null 0.0 0 0.4178135292556882 prophet 1 3 1239956 2017-07-16 7.577937638245066 5.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-17 2.3327766331412603 2.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-18 1.1177181630966935 3.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-19 0.7314798527198692 3.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-20 1.07633531476751 1.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-21 0.73695738948964 2.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-22 4.581899975101967 6.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-23 8.17684796638286 5.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-24 2.9994321164070703 5.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-25 1.839422715715259 3.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-26 1.4944155058157973 2.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-27 1.8659002724609728 4.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-28 1.5381313735361433 3.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-29 5.379627879927045 7.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-30 8.956432149028801 11.0 0 null 0.0 0 0.4219309773649549 prophet 1 3 1239956 2017-07-31 3.7469231936334